# Import thư viện

In [231]:
import numpy as np 
import pandas as pd
import re
from itables import show
from scipy.stats import skew,boxcox_normmax, zscore
from sklearn.preprocessing import StandardScaler, RobustScaler, PowerTransformer, FunctionTransformer, OneHotEncoder
import matplotlib.pyplot as plt
import seaborn as sns
import itables.options as opt
import os
opt.maxBytes = 5000000

# Nạp dữ liệu

In [232]:
train = pd.read_csv('../data/train.csv')
test = pd.read_csv('../data/test.csv')

# Tiền xử lý dữ liệu

## Drop các đặc trưng không cần thiết trong mô hình

In [233]:
# train.drop(['Id', 'Track Name'], axis=1, inplace=True)
# test.drop(['Id', 'Track Name'], axis=1, inplace=True)

## Xử lý dữ liệu thiếu:

In [234]:
train.columns

Index(['Id', 'Artist Name', 'Track Name', 'Popularity', 'danceability',
       'energy', 'key', 'loudness', 'mode', 'speechiness', 'acousticness',
       'instrumentalness', 'liveness', 'valence', 'tempo',
       'duration_in min/ms', 'time_signature', 'Class'],
      dtype='object')

In [235]:
missing_feats = ['Popularity','key','instrumentalness']

for feat in missing_feats:
    global_median = train[feat].median()
    train[feat] = train[feat].fillna(global_median)
    test[feat] = test[feat].fillna(global_median)

In [236]:
train.isna().sum()

Id                    0
Artist Name           0
Track Name            0
Popularity            0
danceability          0
energy                0
key                   0
loudness              0
mode                  0
speechiness           0
acousticness          0
instrumentalness      0
liveness              0
valence               0
tempo                 0
duration_in min/ms    0
time_signature        0
Class                 0
dtype: int64

In [237]:
test.isna().sum()

Id                    0
Artist Name           0
Track Name            0
Popularity            0
danceability          0
energy                0
key                   0
loudness              0
mode                  0
speechiness           0
acousticness          0
instrumentalness      0
liveness              0
valence               0
tempo                 0
duration_in min/ms    0
time_signature        0
dtype: int64

## Xử lý Artist Name:

+ Sửa lỗi ngôn ngữ
+ Dọn dẹp các tên được xem là corrupted (Chứa các kí tự đặt biệt mà ko có các chữ cái)
+ Cắt chuỗi nhóm tên thành từng tên độc lập

In [238]:
#chỉ có chữ
tmp = train.copy()
tmp = tmp[['Id','Artist Name']]
tmp = tmp.drop_duplicates()
show(tmp)

#loại bỏ chữ cái alphabet
not_alphabet = tmp[~tmp['Artist Name'].str.contains(r'(?=.*[A-Za-z])')]
show(not_alphabet)

#có số là được
num_included = tmp[tmp['Artist Name'].str.contains(r'\d')]
show(num_included)

#chỉ có số
num_only = tmp[tmp['Artist Name'].str.isdigit()]
show(num_only)

#gồm số và chữ
num_alphabelt = tmp[tmp['Artist Name'].str.contains(r'(?=.*[A-Za-z])(?=.*\d)')]
show(num_alphabelt)


In [239]:
diff_rows = not_alphabet[~not_alphabet['Artist Name'].isin(num_only['Artist Name'])]
show(diff_rows)

In [240]:
diff_rows = test[test['Artist Name'].isin(diff_rows['Artist Name'])]
show(diff_rows)

## Dựa trên dữ liệu đã bị corrupted trên cả test train ta có thể coi nó như cùng chung format 
**phương hướng xử lí:**
- Trim
- Regex chuỗi gán label đối với nhóm ca sĩ, đồng thời giữ chuỗi gốc đã có nhãn làm tập train.
- Thiết lập quy luật cho input là nếu vocab đó (token) không có trong train thì mặc định embedding là vector 0.

In [247]:
# def explode_artists(df):
#     rows = []
#     for idx, row in df.iterrows():
#         artists = [x.strip() for x in str(row["Artist Name"]).split(",")]
#         for artist in artists:
#             rows.append({
#                 "Original Index": idx,
#                 "Artist Name": artist,
#                 "Class": row.get("Class", None)
#             })
#     return pd.DataFrame(rows)

def optimized_explode_artists(df):
    df_temp = df.copy()
    df_temp["Original Index"] = df_temp.index
    #Vì mỗi artist cách nhau một dấu ,
    df_temp['Artist Name'] = df_temp['Artist Name'].str.split(',')
    #Tách dòng dùng pandas
    df_exploded = df_temp.explode('Artist Name')
    #Bỏ khoảng trắng
    df_exploded['Artist Name'] = df_exploded['Artist Name'].str.strip()
    return df_exploded

Hàm này dùng để tách các Artist ra. Vì trong 1 bài hát có thể có hơn 1 người khác. Mà mỗi artist cách nhau bằng 1 dấu "," ta sẽ tách các Artist này ra và vẫn lưu lại Original Index để tí còn group vào lại dataset.

In [248]:
train_exp = optimized_explode_artists(train)
show(train_exp)

In [250]:
def group_back(df_exp):
    # 1. Lấy danh sách tất cả các cột trừ 2 cột đặc biệt đang xử lý
    cols_to_keep = [c for c in df_exp.columns if c not in ["Original Index", "Artist Name"]]
    
    # 2. Tạo dictionary quy tắc gộp:
    # - Artist Name: gộp và sort lại
    # - Các cột khác: lấy giá trị đầu tiên ('first')
    agg_rules = {c: 'first' for c in cols_to_keep}
    agg_rules["Artist Name"] = lambda x: ", ".join(sorted(set(x)))
    
    return (
        df_exp
        .groupby("Original Index")
        .agg(agg_rules) # Áp dụng quy tắc cho TOÀN BỘ cột
        .reset_index()
    )

train_grouped = group_back(train_exp)
final_train = pd.concat([train_exp, train_grouped], ignore_index=True)
final_train = final_train.drop(columns=["Original Index"], errors='ignore')
final_train = final_train.drop_duplicates().reset_index(drop=True)
print(f"Số dòng ban đầu: {len(train)}")
print(f"Số dòng sau khi làm giàu dữ liệu: {len(final_train)}")
show(final_train)

Số dòng ban đầu: 14396
Số dòng sau khi làm giàu dữ liệu: 15578


# Feature Engineering

In [ ]:
#StandardScaler
StandardScaler_feats = ['Popularity', 'tempo', 'danceability','valence',
                        'energy','speechiness','acousticness',
                        'instrumentalness','liveness']

#Log transformer
log_feats = ['speechiness','acousticness',
            'instrumentalness','liveness']

# #One-hot
# Cat_feats = ['key','mode','time_signature']

In [ ]:
#Tạo sacler
scaler_std = StandardScaler()
pt_loudness = PowerTransformer(method='yeo-johnson')
scaler_robust = RobustScaler()

# =============== Dữ liệu train ===============
#Log transform
train[log_feats] = np.log1p(train[log_feats])

#StandardScaler
train[StandardScaler_feats] = scaler_std.fit_transform(train[StandardScaler_feats])

#Power Transformer
#Nó tự động tìm ra lambda tốt nhất:
#Cần log thì log
#Cần bình phương thì sẽ bình phương
#Xử lý cả âm
train['loudness'] = pt_loudness.fit_transform(train[['loudness']])

#RobustScaler
train[['duration_in min/ms']] = scaler_robust.fit_transform(train[['duration_in min/ms']])


# =============== Dữ liệu test ===============
#Sử dụng các dữ liệu đã fit ở tập train để transform cho tập test
test[log_feats] = np.log1p(test[log_feats])
test[StandardScaler_feats] = scaler_std.transform(test[StandardScaler_feats])
test['loudness'] = pt_loudness.transform(test[['loudness']])
test[['duration_in min/ms']] = scaler_robust.transform(test[['duration_in min/ms']])

# Lưu lại dữ liệu

In [ ]:
exp_dir = "../exps"
if os.path.exists(exp_dir) == False:
    os.makedirs(exp_dir,exist_ok=True)

save_dir = f"{exp_dir}/Preproccessed"
os.makedirs(save_dir,exist_ok=True)

In [ ]:
# train = df.iloc[:14396,:]
# test = df.iloc[14396:,:]

In [ ]:
train.to_csv(f'{save_dir}/exp1_train.csv',index=False)
test.to_csv(f'{save_dir}/exp1_test.csv',index=False)